# Course Creation Example

This notebook demonstrates how to use the `CourseCreator` to generate course ideas and outlines.

## Import and instantiate the CourseCreator class

Initialize a `CourseCreator` instance. All course creation is performed through this object.

In [ ]:
import os
from dotenv import load_dotenv
from openai import OpenAI
load_dotenv()

# Check the key
key = os.getenv("OPENAI_API_KEY")
print(f"Key: {key[:8]}...{key[-4:]}")
# Test a simple API call
client = OpenAI()
try:
    response = client.chat.completions.create(
        model="gpt-4o-mini",  # cheapest model
        messages=[{"role": "user", "content": "Say hello"}],
        max_tokens=5
    )
    print(f"Success! Response: {response.choices[0].message.content}")
except Exception as e:
    print(f"Error: {e}")

In [ ]:
from openai import OpenAI
client = OpenAI()

models_to_test = ["gpt-4o", "o3-mini", "gpt-4.1"]

for model in models_to_test:
    try:
        response = client.chat.completions.create(
            model=model,
            messages=[{"role": "user", "content": "Hi"}],
            #max_tokens=5
        )
        print(f"✓ {model}: works")
    except Exception as e:
        print(f"✗ {model}: {e}")

In [ ]:
import os
from dotenv import load_dotenv
from langchain_google_genai import ChatGoogleGenerativeAI

load_dotenv()

key = os.getenv("GOOGLE_API_KEY")
if key:
    print(f"Key: {key[:8]}...{key[-4:]}")

    llm = ChatGoogleGenerativeAI(model="gemini-2.5-flash", google_api_key=key)
    response = llm.invoke("Say hello")
    print(f"Success! Response: {response.content}")
else:
    print("No GOOGLE_API_KEY found in .env")
    print("Get one free at: https://aistudio.google.com/apikey")

In [25]:
from denario.course import CourseCreator

creator = CourseCreator(project_dir="./course_project", clear_project_dir=False)

Run directory: ./course_project/20251202_182301


In [18]:
import denario.prompts.course_outline as outline_prompts
import denario.prompts.course_idea as idea_prompts

print("--- Course Idea Prompt ---")
print(idea_prompts.course_idea_planner_prompt)
print("\n--- Course Outline Prompt ---")
print(outline_prompts.course_outline_researcher_prompt)

--- Course Idea Prompt ---

Given the topic of interest, the duration of the course, and the audience, make a plan according to the following instructions: 
- Ask idea_maker to generate 5 new course ideas related to the topic of interest.
- Ask idea_hater to critique these ideas for pedagogy, feasibility and audience fit.
- Ask idea_maker to select and improve 2 out of the 5 course ideas given the output of the idea_hater.
- Ask idea_hater to critique the 2 improved ideas. 
- Ask idea_maker to select the best idea out of the 2. 
- Ask idea_maker to report the best idea in the form of a course title with a 5-sentence description. 

The goal of this task is to generate a course idea based on the topic of interest. 
IMPORTANT: The course idea must go beyond generic benefits. It should prioritize **technical depth**, **specific tools**, and **actionable frameworks**.
Investigate which features and tools are important for the topic of interest and use this to guide your decision making.
Don

## Set the course topic, audience, and duration

Specify the subject you want to teach, who the course is for, and how long it will be.

In [ ]:
creator.set_topic(
    topic="ChatGPT Professional Proficiency: From Basics to Advanced Features",
    audience="Professionals in different fields seeking deep proficiency without coding. They want to go from basics in LLMs such as prompt and context to medium-level features. They want to explore a large set of tools currently offered by ChatGPT. ",
    duration="24 hours"
)

creator.show_topic()

## Generate a course idea

Use the `idea_maker` and `idea_hater` agents to brainstorm and refine course ideas.

In [ ]:
# Using gpt-4o-mini (available on lower OpenAI tiers)
#creator.generate_idea()
creator.generate_idea(
    idea_maker_model="gpt-5",
    idea_hater_model="gpt-5-mini",
    planner_model="gpt-5",
    plan_reviewer_model="gpt-5-mini",
    orchestration_model="gpt-5",
    formatter_model="gpt-5-mini",
)
# Original models (require higher OpenAI tier):
# creator.generate_idea(
#     idea_maker_model="gpt-4o",
#     idea_hater_model="o3-mini",
#     planner_model="gpt-4o",
#     plan_reviewer_model="o3-mini",
#     orchestration_model="gpt-4.1",
#     formatter_model="o3-mini",
# )
creator.show_idea()

In [ ]:
# Read and display ideas in sequence to see how they developed
import json
from pathlib import Path
from IPython.display import display, Markdown

# Get the run directory from the creator
run_dir = Path(creator.work_dir)
control_dir = run_dir / "idea_generation_output" / "control"

# Read ideas JSON files (snapshots at each idea_maker step)
ideas_files = sorted(control_dir.glob("ideas_*.json"))

print(f"Found {len(ideas_files)} idea snapshots in {control_dir}\n")

step_map = {0: "Step 1: Initial ideas (5 generated)", 
            1: "Step 3: Improved 2 ideas", 
            2: "Step 5: Best idea selected", 
            3: "Step 6: Final formatted idea"}

for i, ideas_file in enumerate(ideas_files):
    display(Markdown(f"---\n## {step_map.get(i, f'Snapshot {i+1}')}"))
    display(Markdown(f"*File: {ideas_file.name}*"))
    
    with open(ideas_file, 'r') as f:
        ideas = json.load(f)
    
    if isinstance(ideas, list):
        for j, idea in enumerate(ideas):
            # Truncate long ideas for readability
            preview = idea[:3000] + "\n\n...[truncated]" if len(idea) > 1500 else idea
            display(Markdown(f"### Idea {j+1}"))
            print(preview)
            print()
    else:
        print(ideas)

In [13]:
# View idea_hater critiques (steps 2 and 4)
chats_dir = control_dir / "chats"

for step in [2, 4]:
    critique_file = chats_dir / f"chat_output_idea_hater_step_{step}.json"
    if critique_file.exists():
        display(Markdown(f"---\n## Step {step}: idea_hater critique"))
        with open(critique_file, 'r') as f:
            critique = json.load(f)
        # Handle both string and other formats
        critique_str = str(critique)
        preview = critique_str[:6000] + "\n\n...[truncated]" if len(critique_str) > 6000 else critique_str
        print(preview)

---
## Step 2: idea_hater critique

[{'name': 'control_starter', 'content': None, 'timestamp': '2025-12-02 10:57:01', 'cost': {'Agent': ['control_starter'], 'Model': ['gpt-5-2025-08-07'], 'Cost': [0.00555625], 'Prompt Tokens': [2229], 'Completion Tokens': [277], 'Total Tokens': [2506]}}, {'name': '_Group_Tool_Executor', 'content': '\n**Step number:** 2 out of 6.\n \n**Sub-task:** Critique the 5 ideas using a standardized rubric and prescribe fixes\n \n**Agent in charge of sub-task:** `idea_hater`\n \n**Instructions:**\n \nScore each idea on a 1–5 rubric across: scaffolding, pacing (24h realism), lab depth (hands-on vs demo), no-code feasibility, domain adaptability, governance/compliance readiness; submit rubric.csv with scores and 2–3 sentence justification per criterion (max 500–800 words per idea). Mark any idea with average score < 3.0 for drop or radical revision; provide 2–4 concrete, prescriptive improvements per idea (e.g., replace generic Vision demo with PDF-table extraction lab; reallocate 30 minutes from Modu

---
## Step 4: idea_hater critique

[{'name': 'control_starter', 'content': None, 'timestamp': '2025-12-02 11:09:58', 'cost': {'Agent': ['control_starter'], 'Model': ['gpt-5-2025-08-07'], 'Cost': [0.0055625], 'Prompt Tokens': [2234], 'Completion Tokens': [277], 'Total Tokens': [2511]}}, {'name': '_Group_Tool_Executor', 'content': '\n**Step number:** 4 out of 6.\n \n**Sub-task:** Run timeline simulation, rebalance, and perform governance/privacy audit; compare the two\n \n**Agent in charge of sub-task:** `idea_hater`\n \n**Instructions:**\n \n- Mock-teach each revised 24-hour schedule to identify overloaded modules (require > allocated time) and thin labs (insufficient steps to meet objectives); propose specific rebalancing actions per issue; keep critiques within 500–800 words per idea and list prioritized top-5 action items.\n- Conduct a governance/privacy audit for each idea: specify Teams/Enterprise settings (data controls, retention flags, access scopes), where anonymization is required, and add at least three compli

## Generate a course outline

Use the `researcher` agent to create a detailed course outline with modules, learning goals, and takeaways.

In [14]:
# Using gpt-4o-mini (available on lower OpenAI tiers)
#creator.generate_outline()
creator.generate_outline(
    researcher_model="gpt-5",
    planner_model="gpt-5",
    plan_reviewer_model="gpt-5-mini",
    orchestration_model="gpt-5",
    formatter_model="gpt-5-mini", 
)
# Original models (require higher OpenAI tier):
# creator.generate_outline(
#     researcher_model="gpt-4.1-2025-04-14",
#     planner_model="gpt-4.1-2025-04-14",
#     plan_reviewer_model="o3-mini",
#     orchestration_model="gpt-4.1",
#     formatter_model="o3-mini",
# )
creator.show_outline()

Generating course outline...
Created context directory:  /Users/elenahernandez/projects/agents/Denario/examples/course_project/20251202_104234/course_outline_generation_output/context
Generate the course outline based on the course idea provided above.

--------------------------------------------------------------------------------
Setting agents for the session...

           Model       agent    Cost  Prompt Tokens  Completion Tokens  Total Tokens
gpt-5-2025-08-07 plan_setter 0.00630           1240                475          1715

--------------------------------------------------------------------------------
Plan constraints have been logged.

--------------------------------------------------------------------------------

Calling planner...

           Model   agent    Cost  Prompt Tokens  Completion Tokens  Total Tokens
gpt-5-2025-08-07 planner 0.02679           1389               2505          3894
Plan:
   - Step 1:
         * sub-task: Analyze course idea, audience, scope, 

# Document Intelligence & Automation with ChatGPT — 24-hour Intensive (No-Code)

### Overview:
A hands-on, no-code intensive for professionals who must convert messy PDFs, scans, and mixed document bundles into accurate, auditable decisions. The course scaffolds from prompting/context foundations through Vision/OCR extraction, ADA-based normalization/QA, redlining, retrieval-grounded Q&A with Browse, governance, and enterprise deployment. Participants explicitly use Advanced Data Analysis (ADA), Browse, Vision for PDFs/tables/images, image generation, file uploads and multi-file analysis, Memory/Custom Instructions, and Custom GPTs with Knowledge and no-code Actions, plus GPT Store and Teams/Enterprise features.

## 1. Prompting & Context Foundations + Environment Setup (2:30)
### Description:
Establish a reproducible prompting discipline and secure platform posture that anchor the pipeline. Calibrate RTCFCE (Role, Task, Context, Format, Constraints, Examples), ReAct, checklist prompts, and A/B prompt versioning to achieve measurable, testable improvements. Configure Memory and Custom Instructions to encode privacy posture, grounded citation norms, and domain tone. Verify access to ADA, Browse, Vision for PDFs/tables/images, image generation, file uploads/multi-file analysis, and the Custom GPT builder.

### Takeaways:
- Seeded RTCFCE/ReAct prompt library with A/B variants and selection rationale.
- Memory/Custom Instructions that enforce privacy and citation standards.
- A/B evaluation checklist and logging template to reduce variance.

### Learning Goals:
- Participants design RTCFCE and ReAct prompts and run A/B evaluations with logged outcomes.
- Participants configure Memory/Custom Instructions to constrain privacy, tone, and citations.
- Participants verify access to ADA, Browse, Vision, image generation, and multi-file uploads.
- Participants define pass/fail criteria and versioning rules for prompt evolution.

### Exercise Description:
Duration: 75 minutes, Debrief: 30 minutes

Instructor Note (Fallback):
- Primary features: Memory, Custom Instructions, file uploads/multi-file analysis.
- Fallback if Memory is unavailable: paste a standardized “preamble” into each session; store preamble text in the prompt_library.

---

## 2. Vision/OCR for Messy PDFs, Tables, and Images (4:00)
### Description:
Engineer resilient extraction for dirty scans and heterogeneous PDFs using Vision for PDFs/tables/images with multi-file uploads. Address page segmentation, multi-page tables, skew/low contrast, stamps/handwriting, and mixed bundles. Implement error logging and a 5-point QA checklist to triage defects and guide remediation.

### Takeaways:
- Extracted CSV(s) with error_log.csv and a completed 5-point QA checklist.
- Stable prompt patterns for tables/forms and page-level triage.
- Remediation rubric for re-scan, batching, or manual correction.

### Learning Goals:
- Participants batch-upload PDFs/images and extract tables/forms using Vision.
- Participants log OCR anomalies (split/merged cells, header loss, misreads) in error_log.csv.
- Participants apply the 5-point QA checklist to set remediation priorities.
- Participants design fallback prompts and batching strategies for problematic pages.

### Exercise Description:
Duration: 150 minutes, Debrief: 30 minutes

Instructor Note (Fallback):
- Primary features: Vision for PDFs/tables/images, file uploads/multi-file analysis.
- Fallback if Vision degrades: use ADA file preview to ingest text; apply constrained table parsing prompts; provide pre-OCR’d snapshots if required.

---

## 3. ADA Normalization & Reproducibility (3:00)
### Description:
Normalize extracted data to a canonical schema in ADA. Enforce typing, unit harmonization, controlled vocabularies, and schema validation; produce anomaly_report.csv and maintain change_log.csv so every transformation is auditable and reproducible. Emphasize deterministic re-runs and versioned filenames.

### Takeaways:
- normalized.csv with canonical fields/types/units.
- anomaly_report.csv capturing outliers, missingness, and schema violations.
- change_log.csv documenting transformation steps and rationale.

### Learning Goals:
- Participants define canonical schemas and normalization rules (dates, currency, units, taxonomies).
- Participants generate anomaly reports and set acceptance thresholds.
- Participants re-run normalization to verify determinism and document residual variance.
- Participants apply naming/versioning conventions for traceable artifacts.

### Exercise Description:
Duration: 120 minutes, Debrief: 30 minutes

Instructor Note (Fallback):
- Primary features: ADA, file uploads.
- Fallback if ADA is unavailable: use a spreadsheet with validation/filters; replicate steps and justifications in change_log.csv.

---

## 4. Redlining & Document Comparison (2:30)
### Description:
Operationalize redlining using Vision and ADA across contracts, policies, SOPs, and structured appendices. Extract clause/table-level diffs, classify risk-bearing edits, and produce executive-ready summaries. Optionally leverage image generation for annotated highlights aligned with textual diffs.

### Takeaways:
- Redline diffs and a structured change_summary with risk/impact annotations.
- Prompt patterns for section/paragraph/table alignment and comparison.
- Optional visual highlights to accelerate stakeholder review.

### Learning Goals:
- Participants align comparable sections and extract granular diffs via Vision and ADA.
- Participants classify changes by business risk and escalation triggers.
- Participants produce stakeholder-ready redline briefs with optional visual annotations.
- Participants document assumptions for reflowed text and scanned markups.

### Exercise Description:
Duration: 80 minutes, Debrief: 30 minutes

Instructor Note (Fallback):
- Primary features: Vision, ADA, image generation.
- Fallback if image generation is disabled: provide textual diff tables; note highlight coordinates for manual annotation.

---

## 5. Knowledge-backed Q&A with Custom GPTs (3:00)
### Description:
Stand up a Custom GPT with Knowledge files for grounded Q&A and correct abstention. Use Custom Instructions to enforce citations, privacy posture, tone, and safety; configure retrieval options (e.g., chunking/metadata). Build a 10-question retrieval QA suite and log outcomes in retrieval_test_log.csv. Introduce no-code Actions via structured outputs for predictable handoffs.

### Takeaways:
- Custom GPT scaffold with Knowledge uploaded and retrieval tuned for grounded answers.
- A retrieval QA suite with pass/fail results, citations, and abstentions.
- Structured output templates suitable for no-code Actions.

### Learning Goals:
- Participants configure a Custom GPT with Knowledge and enforce citation/abstention rules.
- Participants design and run a retrieval QA suite with quantifiable thresholds.
- Participants produce structured outputs for reliable downstream consumption.
- Participants document tuning levers (chunking, file formats, Knowledge refresh cadence).

### Exercise Description:
Duration: 120 minutes, Debrief: 30 minutes

Instructor Note (Fallback):
- Primary features: Custom GPT builder, Knowledge, Custom Instructions.
- Fallback if builder is unavailable: emulate with ChatGPT + file uploads in-session; maintain retrieval_test_log.csv manually.

---

## 6. Browsing, Grounding, and Citations Under Uncertainty (1:45)
### Description:
Enable Browse to incorporate time-sensitive or external evidence within scoped domains. Practice verification steps, decide when to answer versus abstain, and document link provenance and evidence quality. Integrate browsed evidence with Knowledge-backed responses while preserving auditability.

### Takeaways:
- Browse policy template with domain allowlists and source-quality criteria.
- Citation exemplars with verification notes and link provenance.
- Safe-failure and escalation patterns for ambiguous or out-of-distribution prompts.

### Learning Goals:
- Participants configure Browse within constrained domains and capture traceable citations.
- Participants validate sources and record verification steps aligned to governance.
- Participants implement abstention and escalation when evidence is insufficient or stale.
- Participants integrate Browse and Knowledge responses while preserving provenance.

### Exercise Description:
Duration: 70 minutes, Debrief: 35 minutes

Instructor Note (Fallback):
- Primary features: Browse.
- Fallback if Browse is disabled: use archived pages or pre-downloaded snapshots; log provenance and verification steps manually.

---

## 7. Governance, Privacy, and Auditability for Enterprise (3:30)
### Description:
Translate QA metrics into enforceable governance aligned with Teams/Enterprise data controls, Memory policy, GPT Store policies, artifact versioning, and retention. Draft a governance SOP and privacy checklist; define a risk-rating rubric across document types and legal escalation triggers. Codify audit trails, timestamp/version conventions, and reviewer sign-offs.

### Takeaways:
- Governance SOP and privacy checklist aligned to enterprise controls.
- Audit-trail template and versioning/timestamp conventions.
- Risk-rating rubric with sign-off triggers and escalation criteria.

### Learning Goals:
- Participants author a governance SOP tied to retrieval QA and normalization thresholds.
- Participants complete a privacy checklist and define retention/versioning conventions.
- Participants apply risk ratings and identify legal/contractual sign-off criteria.
- Participants configure Teams/Enterprise sharing and data controls to meet policy.

### Exercise Description:
Duration: 120 minutes, Debrief: 30 minutes

Instructor Note (Fallback):
- Primary features: Teams/Enterprise settings, Memory policy controls.
- Fallback without Teams/Enterprise: simulate with shared drives and manual permission logs; still adopt SOP and audit templates.

---

## 8. Deployment via Teams/Enterprise and GPT Store (1:45)
### Description:
Operationalize internal sharing and optional publication workflows. Configure Teams/Enterprise org sharing, collections, and permissions; evaluate GPT Store norms where publication is permitted. Establish release cadence, change notes, rollback plans, and a consumer SOP to standardize no-code handoffs.

### Takeaways:
- Deployment plan with scoped access/permissions and release/rollback procedures.
- Consumer SOP with stable inputs/outputs and incident response paths.
- Readiness checklist for internal-only versus GPT Store publication.

### Learning Goals:
- Participants configure Teams/Enterprise sharing and least-privilege permission models.
- Participants prepare versioned releases with change notes and rollback plans.
- Participants draft a consumer SOP for safe, repeatable downstream use.
- Participants assess GPT Store publication options against policy constraints.

### Exercise Description:
Duration: 75 minutes, Debrief: 30 minutes

Instructor Note (Fallback):
- Primary features: Teams/Enterprise sharing; GPT Store.
- Fallback if GPT Store is not allowed: finalize internal-only deployment; document deferred publication steps.

---

## 9. Capstone Build: End-to-End Doc-to-Decision Pipeline (1:30)
### Description:
Integrate Vision/OCR extraction, ADA normalization, redlining, Knowledge-backed Q&A with Browse, and governance into a cohesive pipeline. Produce a decision memo with grounded citations and attach all versioned artifacts. Validate performance against predefined QA thresholds and governance rules.

### Takeaways:
- Full pipeline run with linked, versioned artifacts and an audit trail.
- Decision memo with citations and appended governance SOP and privacy checklist.
- Self-assessed pass/fail outcome mapped to rubric thresholds.

### Learning Goals:
- Participants execute the pipeline on a fresh document pack meeting accuracy/governance thresholds.
- Participants assemble and cross-reference artifacts coherently in a decision memo.
- Participants identify limitations and propose prioritized improvements.

### Exercise Description:
Duration: 75 minutes, Debrief: 15 minutes

Instructor Note (Fallback):
- Primary features: Vision, ADA, Custom GPT with Knowledge, Browse, Teams/Enterprise.
- Fallback: apply module-specific fallbacks; document impacts and mitigations in the decision memo.

---

## 10. Defense, Assessment, and Handover (0:30)
### Description:
Defend the capstone pipeline with a concise walkthrough of artifacts, QA metrics, and governance posture. Formalize Teams/Enterprise deployment steps and record pass/fail with rationale. Capture peer/facilitator feedback to inform productionization and scaling.

### Takeaways:
- Peer-reviewed feedback and facilitator rubric scores.
- Documented pass/fail decision, deployment readiness, and risk mitigations.
- Targeted post-course roadmap and recommended follow-ups.

### Learning Goals:
- Participants defend design choices using evidence from logs, metrics, and citations.
- Participants finalize deployment readiness including permissions and rollback plans.
- Participants select follow-up modules to deepen retrieval QA and no-code Actions.

### Exercise Description:
Duration: 20 minutes, Debrief: 10 minutes

---

## Assessment Checkpoints and Pass Thresholds
- Vision/OCR extraction (Module 2): error_log.csv complete; 5-point QA checklist completed; stable extraction patterns on a holdout file set.
- ADA normalization (Module 3): normalized.csv present; anomaly_report.csv triage documented; change_log.csv complete; re-run reproduces outputs.
- Redlining (Module 4): material change detection with risk annotations in change_summary; rationale consistent and traceable to source.
- Knowledge-backed Q&A and Browse (Modules 5–6): retrieval_test_log.csv evidences grounded answers with correct abstentions; citations verifiable; browse_policy followed.
- Governance (Module 7): governance SOP and privacy checklist finalized; audit-trail template adopted; Teams/Enterprise sharing documented.
- Capstone (Modules 9–10): decision memo cites sources, links artifacts, and states pass/fail against thresholds with rationale.

---

## Cross-References
- Modules → Deliverables
  - M1: Prompt library (10 RTCFCE prompts with A/B scores and selection rationale).
  - M2: Extraction and QA pack (extracted.csv, error_log.csv, QA_checklist.md).
  - M3: ADA normalization report (normalized.csv, anomaly_report.csv, change_log.csv).
  - M5: Custom GPT scaffold with Knowledge + retrieval_test_log.csv.
  - M7: Governance SOP + privacy checklist.
  - M9: Capstone decision memo + artifact index.

- Modules → Rubric Thresholds
  - M2 → OCR accuracy and QA completeness.
  - M3 → anomaly rate and reproducibility.
  - M4 → material-change recall and risk annotation completeness.
  - M5–M6 → retrieval groundedness, abstention correctness, citation verification.
  - M7 → governance SOP completeness, privacy checklist, audit-trail adoption.
  - M9–M10 → end-to-end capstone pass/fail.

---

## Evaluation & Sign-off Procedure
- Roles: Facilitator evaluates artifacts against rubric thresholds; peer participant provides secondary review; product owner/team lead signs deployment readiness.
- Recording: Store assessment_rubric_scores.csv and deployment_readiness.md in the cohort folder; record pass/fail with rationale and remediation plan if applicable.
- Remediation: Timeboxed rework; corrective actions captured in change_log.csv and an addendum to the decision memo.

---

## Instructor Prep
- Access checks: Confirm Plus/Teams/Enterprise access to ADA, Browse, Vision, image generation, file uploads/multi-file analysis, Memory/Custom Instructions, and the Custom GPT builder with Knowledge; ensure Teams/Enterprise sharing is enabled or stage a shared-drive fallback.
- Sample datasets: Dirty scans (invoices with stamps/handwriting), multi-page tables, contracts with amendments, policy versions; one document pack per learner.
- Templates staged: prompt_library.csv, error_log.csv, QA_checklist.md, anomaly_report.csv, change_log.csv, retrieval_test_log.csv, governance_SOP.md, privacy_checklist.md, audit_trail_template.csv, deployment_plan.md, decision_memo.md.
- Buffers: Reserve slack in Modules 2, 3, and 7 to absorb OCR variability, normalization rework, and SOP drafting.
- Naming/versioning: Use consistent timestamps and versioning (e.g., idea03_M3_normalized_v1.csv; idea03_M5_retrieval_test_log_v1.csv).

---

### Further Resources for Course Organizers (Preparation)
- OpenAI platform status and features: https://status.openai.com
- Advanced Data Analysis (ADA): https://help.openai.com/en/articles/8554397-advanced-data-analysis
- Vision (PDFs/tables/images): https://platform.openai.com/docs/guides/vision
- Browse capability: https://help.openai.com/en/articles/8554400-browsing
- Custom GPTs and Knowledge: https://help.openai.com/en/articles/8554408-custom-gpts
- Teams/Enterprise features and admin: https://openai.com/enterprise
- GPT Store guidelines and policies: https://openai.com/blog/introducing-the-gpt-store
- NIST AI Risk Management Framework: https://www.nist.gov/itl/ai-risk-management-framework
- Accessibility (WCAG 2.1): https://www.w3.org/WAI/standards-guidelines/wcag/

### Further Resources for Participants (Learning)
- OpenAI Prompt Engineering Guide: https://platform.openai.com/docs/guides/prompt-engineering
- ReAct prompting pattern: https://arxiv.org/abs/2210.03629
- Evaluating LLMs (test suites and metrics): https://arxiv.org/abs/2307.03109
- Practical data cleaning and normalization: https://library.carleton.ca/guides/data-cleaning
- Responsible AI practices (governance basics): https://ai.google/responsibilities/responsible-ai-practices
- Contract redlining primer: https://www.americanbar.org/groups/business_law/publications/committee_newsletters/CL182000/
- Versioning and audit trails in data projects: https://dvc.org/doc/start

Notes to facilitation:
- Explicitly name and demonstrate: ADA, Browse, Vision for PDFs/tables/images, image generation, file uploads/multi-file analysis, Memory/Custom Instructions, Custom GPTs with Knowledge and no-code Actions, GPT Store, and Teams/Enterprise controls.
- Enforce the no-code policy rigorously while leveraging structured outputs, checklists, and rubrics to ensure accuracy, grounded citations, and reproducible workflows.

## Alternative: Set idea manually

If you already have a course idea, you can set it directly and skip the idea generation step.

In [26]:
# Load a specific idea from the JSON file and set it as the course idea
import json

# Path to the ideas JSON file (adjust timestamp as needed)
ideas_json_path = "./course_project/20251202_104234/idea_generation_output/control/ideas_20251202_110836.json"

with open(ideas_json_path, 'r') as f:
    ideas = json.load(f)

# Extract Idea 1 (first item in the list)
idea_1 = ideas[0]
print(f"Loaded Idea 1 ({len(idea_1)} characters)")
print(idea_1[:500] + "..." if len(idea_1) > 500 else idea_1)

# Set this idea for the creator
creator.set_idea(idea=idea_1)
print("\n✓ Idea 1 set successfully")

Loaded Idea 1 (14874 characters)
   - Idea 1: ChatGPT Pro Power User: No-Code Productivity and Analysis — Revised 24-hour Intensive (idea01)
         * What it is: A hands-on, end-to-end 24-hour course for cross-functional professionals to progress from prompt/context fundamentals to medium-level features across ADA, Browse, Vision, Image generation, multi-file analysis, Custom Instructions/Memory, Custom GPTs (Builder, Knowledge, no-code Actions concept), GPT Store, and Teams/Enterprise governance. Incorporates Step 2 critique...

✓ Idea 1 set successfully


In [27]:
# Using gpt-4o-mini (available on lower OpenAI tiers)
##creator.generate_outline()
creator.generate_outline(
    researcher_model="gpt-5",
    planner_model="gpt-5",
    plan_reviewer_model="gpt-5-mini",
    orchestration_model="gpt-5",
    formatter_model="gpt-5-mini", 
)
# Original models (require higher OpenAI tier):
# creator.generate_outline(
#     researcher_model="gpt-4.1-2025-04-14",
#     planner_model="gpt-4.1-2025-04-14",
#     plan_reviewer_model="o3-mini",
#     orchestration_model="gpt-4.1",
#     formatter_model="o3-mini",
# )
creator.show_outline()

Generating course outline...
Created context directory:  /Users/elenahernandez/projects/agents/Denario/examples/course_project/20251202_182301/course_outline_generation_output/context
Generate the course outline based on the course idea provided above.

--------------------------------------------------------------------------------
Setting agents for the session...

           Model       agent    Cost  Prompt Tokens  Completion Tokens  Total Tokens
gpt-5-2025-08-07 plan_setter 0.01676           3973               1179          5152

--------------------------------------------------------------------------------
Plan constraints have been logged.

--------------------------------------------------------------------------------

Calling planner...

           Model   agent    Cost  Prompt Tokens  Completion Tokens  Total Tokens
gpt-5-2025-08-07 planner 0.02656           4122               2141          6263
Plan:
   - Step 1:
         * sub-task: Analyze the course idea and define cor

KeyError: 'name'

In [ ]:
##creator.set_idea(idea=r"""
## Course Title: ChatGPT Premium Unlocked: Tools and Techniques for Business Excellence
## 
##- This course offers a comprehensive exploration of the advanced tools available in the ChatGPT premium seat, focusing on features like execution flows and custom instructions.
##- Participants will engage in interactive workshops and analyze real-world business case studies to enhance practical relevance and applicability.
##- Each module includes in the end 1 or 2 practical exercises to apply the tools learned.
##- The course inlcudes some ethical AI practices, providing examples directly linked to business implications to ensure responsible usage.
##- Scaffolding steps, such as a mini project or simulation exercise, are included to facilitate the transition from tool exploration to practical application.
##- Workshop segments are mapped to specific business outcomes, such as increased operational efficiency, to clearly measure the learning impact and ensure actionable insights.
##
## """)
##
##creator.generate_outline()
##creator.show_outline()

## Full workflow in one call

Alternatively, run the entire workflow (idea + outline generation) with a single method call.

In [ ]:
# creator2 = CourseCreator(project_dir="./another_course", clear_project_dir=True)
# creator2.set_topic(
#     topic="Data Visualization with Python",
#     audience="Data analysts familiar with Excel",
#     duration="1 day (4 hours)"
# )
# creator2.run()  # Generates both idea and outline
# creator2.show_outline()